# Thai Sentence Segmentation with mT5

## Setup

In [4]:
import pandas as pd
import glob
import sys
import os

## Import Data

In [9]:
# The dataset lst20 with config lst20 requires manual data.
#  You need to:
# 1. Manually download `AIFORTHAI-LST20Corpus.tar.gz` from https://aiforthai.in.th/corpus.php (login required; website mostly in Thai)
# 2. Extract the .tar.gz; this will result in folder `LST20Corpus`
# The <path/to/folder> can e.g. be `~/Downloads/LST20Corpus`.
# lst20 can then be loaded using the following command `datasets.load_dataset("lst20", data_dir="<path/to/folder>")`.

In [ ]:
from google.colab import  drive
drive.mount('/content/drive')

Mounted at /content/drive


In [ ]:
def get_df_limittoken(filepath,num_token=150):
    keyList = ['tokens', 'boundary']
    data = {key: [] for key in keyList}
    for filename in glob.glob(os.path.join(filepath, '*.txt')):
        with open(os.path.join(os.getcwd(), filename), 'r') as f:
            column1 = []
            column2 = []
            count_token = 0
            for i,line in enumerate(f.readlines()):
                entry = line.rstrip('\n').split('\t')
                if(len(entry)!=4):  # ถ้าเป็นวรรคแบ่งประโยค
                    entry = [' ','space','space','space']
                if(count_token==num_token):
                    data["tokens"].append(column1)
                    data["boundary"].append(column2)
                    column1 = []
                    column2 = []
                    count_token = 0
                column1.append(str(entry[0]).replace('_',' '))
                #replace _ with space
                if(entry[3]=='space'):
                    # column5.append('SEP')
                    column2.append('|')
                else:               
                    # column5.append('N')
                    column2.append(str(entry[0]).replace('_',' '))
                count_token+=1
            data["tokens"].append(column1)
            data["boundary"].append(column2)
    df = pd.DataFrame.from_dict(data)
    return df

In [ ]:
train_df = get_df_limittoken('/content/drive/My Drive/IS/LST_20/train/')
dev_df = get_df_limittoken('/content/drive/My Drive/IS/LST_20/dev/')
test_df = get_df_limittoken('/content/drive/My Drive/IS/LST_20/test/')

In [ ]:
def source(text):
  new_text = ''.join(text)
  # new_text = "segment sentence: " + new_text
  new_text = "segment each sentence with |: " + new_text
  return new_text

def target(text):
  return ''.join(text)

def convert_text(df):
  df['source_text'] = df['tokens'].apply(source)
  df['target_text'] = df['boundary'].apply(target)

  return df[['source_text', 'target_text']]

In [ ]:
train_df = convert_text(train_df)
train_df

source_text  \
0      segment each sentence with |: เผยเจ็ต ลี และแจ...   
1      segment each sentence with |: เป็นหนังแอ็กชั่น...   
2      segment each sentence with |: นายกรัฐมนตรีญี่ป...   
3      segment each sentence with |: สาวม.ปลายสาธารณร...   
4      segment each sentence with |:  2005 จากไอซ์แลน...   
...                                                  ...   
20396  segment each sentence with |: กกต.ยื้อไม่มั่นใ...   
20397  segment each sentence with |: เพิ่มเติมหรือไม่...   
20398  segment each sentence with |: ไม่ได้เป็นการดิส...   
20399  segment each sentence with |: เหตุใดถึงไม่เดิน...   
20400  segment each sentence with |: ตำแหน่งในกระทรวง...   

                                             target_text  
0      เผยเจ็ต ลี และแจ็กกี้ ชาน จะแสดงหนังร่วมกันเป็...  
1      เป็นหนังแอ็กชั่นที่มีฉากแสดงศิลปะการต่อสู้|อย่...  
2      นายกรัฐมนตรีญี่ปุ่นเรียกร้องให้จีนกดดันเกาหลีเ...  
3      สาวม.ปลายสาธารณรัฐเช็กคว้ามงกุฎมิสเวิลด์ 2006|...  
4       2005 จากไอซ์แลนด์ คูชาโรวานับเป็นสาวงามจากยุโ...  
...                                                  ...  
20396  กกต.ยื้อไม่มั่นใจลงมติ 28 ส.ส.ปชป.ถือหุ้นทัน 1...  
20397  เพิ่มเติมหรือไม่ เพราะหลังจากการศึกษาแล้วก็ต้อ...  
20398  ไม่ได้เป็นการดิสเครดิต สำหรับเรื่องดังกล่าวกกต...  
20399  เหตุใดถึงไม่เดินทางเข้ามาชี้แจง|แต่เรื่องของคด...  
20400  ตำแหน่งในกระทรวงดังกล่าว ที่ประชุมกกต.จึงมีควา...  

[20401 rows x 2 columns]

In [ ]:
dev_df = convert_text(dev_df)
dev_df

source_text  \
0     segment each sentence with |: "มาร์ค"ลั่นไม่อุ...   
1     segment each sentence with |: ก็ต้องไปตรวจสอบว...   
2     segment each sentence with |:  แต่เท่าที่ตนติด...   
3     segment each sentence with |: ร้องมา ไม่มีการท...   
4     segment each sentence with |: กันยาก ตนก็เข้าใ...   
...                                                 ...   
1858  segment each sentence with |: ของไมเคิล ด้าน อ...   
1859  segment each sentence with |:  อาวล์ บี แดร์ ท...   
1860       segment each sentence with |: ถึง 27 ล้านคน    
1861  segment each sentence with |: มอร์แกน ฟรีแมน เ...   
1862  segment each sentence with |: เปิดเผยเอาก็ตอนท...   

                                            target_text  
0     "มาร์ค"ลั่นไม่อุ้มคนทุจริต ฉุนงาบหัวคิวชุมชนพอ...  
1     ก็ต้องไปตรวจสอบว่า ราคาแพงหรือไม่ ขัดกับความต้...  
2      แต่เท่าที่ตนติดตามการทำงานของนายกอร์ปศักดิ์ โ...  
3     ร้องมา ไม่มีการที่จะไปฟอกใครทั้งสิ้น" นายอภิสิ...  
4     กันยาก ตนก็เข้าใจ บางครั้ง ส.ส. นักการเมือง แก...  
...                                                 ...  
1858  ของไมเคิล|ด้าน อัล ชาร์ปตัน นักเคลื่อนไหวเพื่อ...  
1859   อาวล์ บี แดร์ ที่เคยสร้างชื่อให้กับไมเคิลสมัย...  
1860                                     ถึง 27 ล้านคน|  
1861  มอร์แกน ฟรีแมน เตรียมวิวาห์กับหลานสะใภ้|ดาราผิ...  
1862  เปิดเผยเอาก็ตอนที่ฟรีแมนเตรียมจะหย่าร้างกับภรร...  

[1863 rows x 2 columns]

In [ ]:
test_df = convert_text(test_df)
test_df

source_text  \
0     segment each sentence with |: ม็อบสมาพันธ์ชุมช...   
1     segment each sentence with |: ความเป็นจริง และ...   
2     segment each sentence with |: สามารถหาคนค้ำประ...   
3     segment each sentence with |: ตำรวจกระจายกำลัง...   
4     segment each sentence with |: วิเชียรพจน์โพธิ์...   
...                                                 ...   
1650  segment each sentence with |: กีฬาในการแข่งขัน...   
1651  segment each sentence with |: เพื่อใช้เป็นชุดน...   
1652  segment each sentence with |: ครั้งที่ 1, เอเช...   
1653  segment each sentence with |: "เฮียฮ้อ"ลุย ปรั...   
1654  segment each sentence with |: ใต้กลยุทธ์คล่องต...   

                                            target_text  
0     ม็อบสมาพันธ์ชุมชนบุกทำเนียบทวงคำตอบนายกฯ|เมื่อ...  
1     ความเป็นจริง และแก้ปัญหาเรื่องบัตรเครดิต รถยนต...  
2     สามารถหาคนค้ำประกันได้ จึงต้องให้พิจารณาประเด็...  
3     ตำรวจกระจายกำลังตามจุดต่างๆ โดยรอบศาลฎีกา ก่อน...  
4     วิเชียรพจน์โพธิ์ศรี รักษาราชการแทนผู้บัญชาการต...  
...                                                 ...  
1650  กีฬาในการแข่งขันกีฬาระดับนานาชาติ 15 รายการในร...  
1651  เพื่อใช้เป็นชุดนักกีฬาทีมชาติไทยในการเข้าร่วมก...  
1652  ครั้งที่ 1, เอเชียนเกมส์ครั้งที่ 16, เอเชียนบี...  
1653  "เฮียฮ้อ"ลุย ปรับอาวอง|เพราะเกิดวิกฤติเศรษฐกิจ...  
1654               ใต้กลยุทธ์คล่องตัว อิสระ หลากหลาย".|  

[1655 rows x 2 columns]

# T5

In [ ]:
# Check whether Colab is connected to GPU.  
gpu_info = !nvidia-smi
gpu_info = '\n'.join(gpu_info)
if gpu_info.find('failed') >= 0:
  print('Not connected to a GPU')
else:
  print(gpu_info)

Mon Nov 28 03:11:03 2022       
+-----------------------------------------------------------------------------+
| NVIDIA-SMI 460.32.03    Driver Version: 460.32.03    CUDA Version: 11.2     |
|-------------------------------+----------------------+----------------------+
| GPU  Name        Persistence-M| Bus-Id        Disp.A | Volatile Uncorr. ECC |
| Fan  Temp  Perf  Pwr:Usage/Cap|         Memory-Usage | GPU-Util  Compute M. |
|                               |                      |               MIG M. |
|===============================+======================+======================|
|   0  Tesla T4            Off  | 00000000:00:04.0 Off |                    0 |
| N/A   37C    P8     9W /  70W |      0MiB / 15109MiB |      0%      Default |
|                               |                      |                  N/A |
+-------------------------------+----------------------+----------------------+
                                                                               
+-------

In [ ]:
!pip install --upgrade simplet5

In [ ]:
# import
from simplet5 import SimpleT5

# instantiate
model = SimpleT5()

# load (supports t5, mt5, byT5 models)
model.from_pretrained("mt5","google/mt5-small")

INFO:pytorch_lightning.utilities.seed:Global seed set to 42


Downloading:   0%|          | 0.00/82.0 [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/4.11M [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/99.0 [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/553 [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/1.12G [00:00<?, ?B/s]

In [ ]:
# train
model.train(train_df = train_df, # pandas dataframe with 2 columns: source_text & target_text
            eval_df = test_df, # pandas dataframe with 2 columns: source_text & target_text
            source_max_token_len = 150, 
            target_max_token_len = 150,
            batch_size = 8,
            max_epochs = 3,
            use_gpu = True,            
            outputdir = "outputs",
            early_stopping_patience_epochs = 0,
            precision = 32
            )

INFO:pytorch_lightning.utilities.distributed:GPU available: True, used: True
INFO:pytorch_lightning.utilities.distributed:TPU available: False, using: 0 TPU cores
INFO:pytorch_lightning.utilities.distributed:IPU available: False, using: 0 IPUs
INFO:pytorch_lightning.accelerators.gpu:LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]
INFO:pytorch_lightning.callbacks.model_summary:
  | Name  | Type                        | Params
------------------------------------------------------
0 | model | MT5ForConditionalGeneration | 300 M 
------------------------------------------------------
300 M     Trainable params
0         Non-trainable params
300 M     Total params
1,200.707 Total estimated model params size (MB)


Validation sanity check: 0it [00:00, ?it/s]

INFO:pytorch_lightning.utilities.seed:Global seed set to 42


Training: 0it [00:00, ?it/s]

Validating: 0it [00:00, ?it/s]

Validating: 0it [00:00, ?it/s]

Validating: 0it [00:00, ?it/s]

In [ ]:
# Download the trained model to Drive
# !zip -r /content/mT5-small-eng_prompt2.zip /content/outputs/simplet5-epoch-2-train-loss-0.3901-val-loss-0.1989
# !cp mT5-small-eng_prompt2.zip /content/drive/MyDrive

  adding: content/outputs/simplet5-epoch-2-train-loss-0.3901-val-loss-0.1989/ (stored 0%)
  adding: content/outputs/simplet5-epoch-2-train-loss-0.3901-val-loss-0.1989/tokenizer.json (deflated 76%)
  adding: content/outputs/simplet5-epoch-2-train-loss-0.3901-val-loss-0.1989/pytorch_model.bin (deflated 24%)
  adding: content/outputs/simplet5-epoch-2-train-loss-0.3901-val-loss-0.1989/tokenizer_config.json (deflated 33%)
  adding: content/outputs/simplet5-epoch-2-train-loss-0.3901-val-loss-0.1989/spiece.model (deflated 46%)
  adding: content/outputs/simplet5-epoch-2-train-loss-0.3901-val-loss-0.1989/config.json (deflated 45%)
  adding: content/outputs/simplet5-epoch-2-train-loss-0.3901-val-loss-0.1989/special_tokens_map.json (deflated 34%)


# Prediction

In [ ]:
# load trained T5 model
model.load_model("mt5", trained_model, use_gpu=True)

In [ ]:
text = 'segment sentence: ตั้งใจของตนเอง ส่วนผู้ที่จะทำโผแต่งตั้งโยกย้าย ต้องเป็นไปตามกฎหมาย อัศวินข้องใจ"วรวุฒิ"ใช้รถของกลางดีเอสไอ พล.ต.ท.อัศวิน ขวัญเมือง ผู้ช่วย ผบ.ตร. หนึ่งในชุดคลี่คลายคดีลอบยิงนายสนธิ เปิดเผยว่า เมื่อช่วงเช้าที่ผ่านมา ได้ส่งกำลังไปค้นบ้านแม่ยายของ ส.ต.ท.วรวุฒิมุ่งสันติ ตำรวจสังกัดกองบัญชาการตำรวจปราบปรามยาเสพติด (บช.ปส.) ย่านลาดปลาเค้า พบรถยนต์ยี่ห้อเชฟโรเลต รุ่นซาฟีรา สีบรอนซ์ หมายเลขทะเบียน ศว 8051 กรุงเทพมหานคร ซึ่งเป็นทะเบียนปลอม โดยรถคันนี้มีหมายเลขทะเบียนที่แท้จริงคือ กษ 3737 เชียงใหม่ ผู้ครอบครองชื่อ นายชาญณรงค์ มูเซอ ผู้ต้องหาคดีค้าเฮโรอีน ซึ่งกรมสอบสวนคดีพิเศษ'
model.predict(text)

['ตั้งใจของตนเอง ส่วนผู้ที่จะทําโผแต่งตั้งโยกย้าย ต้องเป็นไปตามกฎหมาย|อัศวินข้องใจ"วรวุฒิ"ใช้รถของกลางดีเอสไอ|พล.ต.ท.อัศวิน ขวัญเมือง ผู้ช่วย ผบ.ตร. หนึ่งในชุดคลี่คลายคดีลอบยิงนายสนธิ เปิดเผยว่า เมื่อช่วงเช้าที่ผ่านมา ได้ส่งกําลังไปค้นบ้านแม่ยายของ ส.ต.ท.วรวุฒิมุ่งสันติ ตํารวจสังกัดกองบัญชาการตํารวจปราบปรามยาเสพติด (บช.ปส.) ย่านลาดปลาเค้า พบรถยนต์ยี่ห้อเชฟโรเลต รุ่นซาฟีรา สีบรอนซ์ หมายเลขทะเบียน ศว 8051 กรุงเทพมหานคร ซึ่งเป็นทะเบียนปลอม โดยรถคันนี้มีหมายเลขทะเบียนที่แท้จริงคือ กษ 3737 เชียงใหม่ ผู้ครอบครองชื่อ นายชาญณรงค์ มูเซอ ผู้ต้องหาคดีค้าเฮโรอีน ซึ่งกรมสอบสวนคดีพิเศษ']

In [ ]:
model.predict('''segment sentence: ได้มีโอกาสออกมาเปิดใจเป็นครั้งแรก ในรายการ ตกมันส์บันเทิง ทางช่อง 9 MCOT HD สำหรับนักแสดงสาวระดับตัวแม่ของวงการบันเทิง บุ๋ม-ปนัดดา วงศ์ผู้ดี หลังจากที่ชื่อของเธอถูกโยงเข้ากับกรณีกระแสข่าวลือ ดาราสาวท้องแก่ใกล้คลอด ซึ่งกำลังเป็นที่จับตามองอยู่ ณ ขณะนี้
โดย บุ๋ม ปนัดดา ได้ชี้แจงรายละเอียดเกี่ยวกับกระแสฟีดแบคที่มาถึงตัวเธอ รวมทั้งเรื่องราวความสัมพันธ์กับสามีหุ่นล่ำ ก็อต-อธิป อนันทวรรณ ที่ได้เข้าพิธีวิวาห์อย่างเรียบง่ายไปเมื่อประมาณเกือบ 2 ปีก่อน...
ตั้งท้องจริงไหม ?
"ใช่ค่ะ แต่ที่ผ่านมาไม่มีใครทัก และตัวบุ๋มเองก็ไม่ได้ปิด อีกอย่างวัยนี้ท้องได้ก็บุญแล้ว เพราะอายุ 46 เป็นการท้องแบบธรรมชาติด้วย ซึ่งนั่นจึงเป็นอีกหนึ่งเหตุผลที่บุ๋มไม่ได้เล่าให้ใครฟัง เพราะบุ๋มอยากให้น้องแข็งแรงสมบูรณ์ที่สุดก่อน บุ๋มทราบว่าตัวเองตั้งท้องเมื่อประมาณช่วง 4 เดือนกว่าๆ น้องเป็นเด็กผู้ชาย กำหนดคลอดพรุ่งนี้ (22 พ.ย. 65)"
"เรื่องการแต่งงาน บุ๋มแต่งมาตั้งนานแล้วค่ะ 2 ปีแล้ว และเพิ่งมาท้อง ฝ่ายชายอยากมีลูก เขาอยากมีมานานแล้ว ไม่ใช่ความผิดพลาด ตอนที่รู้ว่าตัวเองตั้งท้อง มีคำถามในหัวเยอะมากว่าเราจะทำงานยังไง เนื่องจากเราเป็นคนบ้างาน และลูกจะแข็งแรงไหม บุ๋มถึงขั้นต้องส่งเลือดไปเช็กที่อเมริกา และพอรู้ว่าน้องแข็งแรงก็เหลือแค่ลุ้นว่าท้องจะใหญ่เมื่อไหร่ เพราะแม้กระทั่งช่วง 7-8 เดือนก็ยังไม่มีใครทัก จนกระทั่งถึงช่วงลอยกระทง สามีถามว่าคนต่อไปเมื่อไหร่ดี เขาอยากมีลูก แต่พอเขาเห็นอัลตร้าซาวด์ว่าเป็นลูกชายและหน้าเหมือนเขา เขาก็ยิ้มหน้าบานแล้ว"
"คลอดพรุ่งนี้เช้านะคะ ตื่นเต้นมาก คือบุ๋มท้องลูกคนนี้ห่างกับน้องอันดาตั้ง 16 ปี (ยิ้ม) ส่วนชื่อก็เดี๋ยวรอดูคุณพ่อเขาอีกทีว่าจะยังไง เพราะเขาค่อนข้างมีความเชื่อเรื่องนี้ และอาการแพ้ท้องต่างๆ ก็น้อยนะคะ ส่วนใหญ่เป็นแค่ง่วงนอน กับอยากกินข้าวไข่เจียว"''')

['ได้มีโอกาสออกมาเปิดใจเป็นครั้งแรก ในรายการ ตกมันส์บันเทิง ทางช่อง 9 MCOT HD สําหรับนักแสดงสาวระดับตัวแม่ของวงการบันเทิง บุ๋ม-ปนัดดา วงศ์ผู้ดี หลังจากที่ชื่อของเธอถูกโยงเข้ากับกรณีกระแสข่าวลือ ดาราสาวท้องแก่ใกล้คลอด ซึ่งกําลังเป็นที่จับตามองอยู่ ณ ขณะนี้ โดย บุ๋ม ปนัดดา ได้ชี้แจงรายละเอียดเกี่ยวกับกระแสฟีดแบคที่มาถึงตัวเธอ รวมทั้งเรื่องราวความสัมพันธ์กับสามีหุ่นล่ํา ก็อต-อธิป อนันทวรรณ ที่ได้เข้าพิธีวิวาห์อย่างเรียบง่ายไปเมื่อประมาณเกือบ 2 ปีก่อน...|ตั้งท้องจริงไหม?|"ใช่ค่ะ แต่ที่ผ่านมาไม่มีใครทัก และตัวบุ๋มเองก็ไม่ได้ปิด อีกอย่างวัยนี้ท้องได้ก็บุญแล้ว เพราะอายุ 46 เป็นการท้องแบบธรรมชาติด้วย ซึ่งนั่นจึงเป็นอีกหนึ่งเหตุผลที่บุ๋มไม่ได้เล่าให้ใครฟัง เพราะบุ๋มอยากให้น้องแข็งแรงสมบูรณ์ที่สุดก่อน บุ๋มทราบว่าตัวเองตั้งท้องเมื่อประมาณช่วง 4 เดือนกว่าๆ น้องเป็นเด็กผู้ชาย กําหนดคลอดพรุ่งนี้ (22 พ.ย. 65)"|"เรื่องการแต่งงาน บุ๋มแต่งมาตั้งนานแล้วค่ะ 2 ปีแล้ว และเพิ่งมาท้อง ฝ่ายชายอยากมีลูก เขาอยากมีมานานแล้ว|และเพิ่งมาท้อง']

In [ ]:
model.predict(''' 
ริชี สุนัค กลายเป็นนายกฯ อังกฤษ เชื้อสายเอเชียคนแรก
นายริชี สุนัค ได้รับเสียงสนับสนุนจาก ส.ส. พรรคคอนเซอร์เวทีฟท่วมท้น ให้รับตำแหน่งหัวหน้าพรรคและนายกรัฐมนตรีต่อจากนางลิซ ทรัสส์ หลังอยู่ในตำแหน่งเพียง 44 วัน ทำให้เขากลายเป็น นายกรัฐมนตรีเชื้อสายเอเชียคนแรกของสหราชอาณาจักร''')

['ริชี สุนัค กลายเป็นนายกฯ อังกฤษ เชื้อสายเอเชียคนแรก|นายริชี สุนัค ได้รับเสียงสนับสนุนจาก ส.ส. พรรคคอนเซอร์เวทีฟท่วมท้น ให้รับตําแหน่งหัวหน้าพรรคและนายกรัฐมนตรีต่อจากนางลิซ ทรัสส์ หลังอยู่ในตําแหน่งเพียง 44 วัน ทําให้เขากลายเป็น นายกรัฐมนตรีเชื้อสายเอเชียคนแรกของสหราชอาณาจักร|']

In [ ]:
model.predict("มึงเคยร้องไห้เพราะทำอะไรไม่เก่งซักอย่างป้ะ กัญชามีความจำเป็นอะไรต้องมาอยู่ในอาหารวะ โรงพยาบาลเป็นสถานที่หนึ่งที่คำว่า positive มีความหมายในเชิงไม่ดี")

['มึงเคยร้องไห้เพราะทําอะไรไม่เก่งซักอย่างป้ะ กัญชามีความจําเป็นอะไรต้องมาอยู่ในอาหารวะ|โรงพยาบาลเป็นสถานที่หนึ่งที่คําว่า positive มีความหมายในเชิงไม่ดี มีความหมายในเชิงไม่ดี']

In [ ]:
model.predict("ไอเดียนี้มาจากคณะอนุกรรมการอนุรักษ์พลังงาน (Energy Conservation Subcommittee) ซึ่งอยู่ภายใต้กระทรวงเศรษฐกิจ, การค้าและอุตสาหกรรมของญี่ปุ่น โดยจะมุ่งเน้นไปที่การควบคุมการใช้พลังงานของเครื่องใช้ไฟฟ้าประเภทเครื่องปรับอากาศของประชาชนในช่วงเวลาที่มีการใช้พลังงานไฟฟ้าสูงเกินกว่าที่ระบบจะสามารถจ่ายไหวซึ่งสุ่มเสี่ยงที่จะทำให้เกิดไฟดับเป็นวงกว้าง")[0].split('|')

['ไอเดียนี้มาจากคณะอนุกรรมการอนุรักษ์พลังงาน (Energy Conservation Subcommittee) ซึ่งอยู่ภายใต้กระทรวงเศรษฐกิจ, การค้าและอุตสาหกรรมของญี่ปุ่น โดยจะมุ่งเน้นไปที่การควบคุมการใช้พลังงานของเครื่องใช้ไฟฟ้าประเภทเครื่องปรับอากาศของประชาชนในช่วงเวลาที่มีการใช้พลังงานไฟฟ้าสูงเกินกว่าที่ระบบจะสามารถจ่ายไหวซึ่งสุ่มเสี่ยงที่จะทําให้เกิดไฟดับเป็นวงกว้าง',
 '']

In [ ]:
txt = '''องค์โชกุนทรงเป็นสตรีรูปร่างสูง มีพระเกศายาวสลวยสีม่วงถักเป็นเปียยาวมีปิ่นปักผมอยู่พระเศียรฝั่งขวา มีริบบิ้นสีแดงเข้มชิ้นเล็กเป็นสายรัดพระศอ ฉลองพระองค์เป็นชุดกิโมโนมีลวดลายหลากแบบเป็นทั้งสีม่วงและแดงเข้ม มีตราแผ่นดินอินาสึมะรัดอยู่กับผ้ารัดพระองค์โอบิในตำแหน่งใต้พระถันขวา ที่พระเพลามีถุงน่องสวมยาวขึ้นมาถึงพระอูรุตัดช่องรูปข้าวหลามตัดเล็กๆด้านบน ด้านหลังของฉลองพระองค์มีโบว์สีแดงเข้มพร้อมพู่ ฉลองพระบาทข้างขวามีดอกไม้สีม่วงอ่อนประดับอยู่สองดอก'''
model.predict(txt)[0].split('|')

['องค์โชกุนทรงเป็นสตรีรูปร่างสูง มีพระเกศายาวสลวยสีม่วงถักเป็นเปียยาวมีปิ่นปักผมอยู่พระเศียรฝั่งขวา มีริบบิ้นสีแดงเข้มชิ้นเล็กเป็นสายรัดพระศอ',
 'ฉลองพระองค์เป็นชุดกิโมโนมีลวดลายหลากแบบเป็นทั้งสีม่วงและแดงเข้ม มีตราแผ่นดินอินาสึมะรัดอยู่กับผ้ารัดพระองค์โอบิในตําแหน่งใต้พระถันขวา ที่พระเพลามีถุงน่องสวมยาวขึ้นมาถึงพระอูรุตัดช่องรูปข้าวหลามตัดเล็กๆด้านบน',
 'ด้านหลังของฉลองพระองค์มีโบว์สีแดงเข้มพร้อมพู่ ฉลองพระบาทข้างขวามีดอกไม้สีม่วงอ่อนประดับอยู่สองดอก']

# Evaluation

In [ ]:
# load trained T5 model
model.load_model("mt5", '/content/outputs/simplet5-epoch-2-train-loss-0.3901-val-loss-0.1989', use_gpu=True)

In [ ]:
test_df

source_text  \
0     segment each sentence with |: ม็อบสมาพันธ์ชุมช...   
1     segment each sentence with |: ความเป็นจริง และ...   
2     segment each sentence with |: สามารถหาคนค้ำประ...   
3     segment each sentence with |: ตำรวจกระจายกำลัง...   
4     segment each sentence with |: วิเชียรพจน์โพธิ์...   
...                                                 ...   
1650  segment each sentence with |: กีฬาในการแข่งขัน...   
1651  segment each sentence with |: เพื่อใช้เป็นชุดน...   
1652  segment each sentence with |: ครั้งที่ 1, เอเช...   
1653  segment each sentence with |: "เฮียฮ้อ"ลุย ปรั...   
1654  segment each sentence with |: ใต้กลยุทธ์คล่องต...   

                                            target_text  
0     ม็อบสมาพันธ์ชุมชนบุกทำเนียบทวงคำตอบนายกฯ|เมื่อ...  
1     ความเป็นจริง และแก้ปัญหาเรื่องบัตรเครดิต รถยนต...  
2     สามารถหาคนค้ำประกันได้ จึงต้องให้พิจารณาประเด็...  
3     ตำรวจกระจายกำลังตามจุดต่างๆ โดยรอบศาลฎีกา ก่อน...  
4     วิเชียรพจน์โพธิ์ศรี รักษาราชการแทนผู้บัญชาการต...  
...                                                 ...  
1650  กีฬาในการแข่งขันกีฬาระดับนานาชาติ 15 รายการในร...  
1651  เพื่อใช้เป็นชุดนักกีฬาทีมชาติไทยในการเข้าร่วมก...  
1652  ครั้งที่ 1, เอเชียนเกมส์ครั้งที่ 16, เอเชียนบี...  
1653  "เฮียฮ้อ"ลุย ปรับอาวอง|เพราะเกิดวิกฤติเศรษฐกิจ...  
1654               ใต้กลยุทธ์คล่องตัว อิสระ หลากหลาย".|  

[1655 rows x 2 columns]

In [ ]:
predicted = ''
for i in test_df['source_text']:
  result = model.predict(i)[0].replace( 'ํา',"ำ")
  predicted += result

In [ ]:
predicted

'ม็อบสมาพันธ์ชุมชนบุกทำเนียบทวงคำตอบนายกฯ เมื่อเวลา 11.00 น. วันนี้(17 ส.ค.) นายจำรัส อินทุมาร ประธานสมาพันธ์ชุมชนแห่งประเทศไทยพร้อมตัวแทนประชาชนประมาณ 50 คน ได้เดินทางมมาที่ทำเนียบรัฐบาล เพื่อติดตามเร่งรัดความคืบหน้าที่ได้ร้องเรียนให้รัฐบาลช่วยเหลือทุนประกอบอาชีพให้ประชาชน ตามโครงการสร้างคน สร้างงาน สร้างรายได้ ตามหลักปรัชญาเศรษฐกิจพอเพียง กลุ่มละ 1 ล้านบาท รวมทั้งให้ยุติการบังคับคดีเกี่ยวกับที่อยู่อาศัย โดยให้ธนาคารของรัฐไถ่ถอนหรือซื้อคืนบ้าน ที่ทำกินให้กับประชาชน และผ่อนส่งราคาที่เป็นธรรมกับธนาคารของรัฐ และอนุญาตให้กู้เงินใช้หนี้นอกระบบให้กับประชาชนตามที่มีหนี้สินตามความเป็นจริง และแก้ปัญหาเรื่องบัตรเครดิต รถยนต์ รถมอเตอร์ไซค์ ที่ใช้ประกอบอาชีพจะโดนยึด เพื่อจะได้ใช้ประกอบอาชีพต่อไปได้|นายจำรัส กล่าวว่า ขอให้นายอภิสิทธิ์ เวชชาชีวะ นายกรัฐมนตรี มีบัญชาไปยังนายกอร์ปศักดิ์ สภาวสุ รองนายกรัฐมนตรี นายกรณ์ จาติกวณิช รมว.คลัง ดำเนินการช่วยเหลือประชาชนผู้เดือดร้อน อีกทั้งนายกรณ์ เคยระบุว่า จะให้มีการตั้งธนาคารชุมชนเพื่อช่วยเหลือประชาชนที่ได้รับความเดือดร้อน ซึ่งตนเห็นด้วยที่จะมีการดำเนินการใ

In [ ]:
with open('predicted-mt5-small-eng_prompt2.txt', 'w') as f:
  f.write(predicted)
!cp 'predicted-mt5-small-eng_prompt2.txt' '/content/drive/MyDrive/NLP 3 Project'

In [ ]:
gold = ''
for i in test_df['target_text']:
  gold += i

In [ ]:
gold

'ม็อบสมาพันธ์ชุมชนบุกทำเนียบทวงคำตอบนายกฯ|เมื่อเวลา 11.00 น. วันนี้(17 ส.ค.) นายจำรัส อินทุมาร ประธานสมาพันธ์ชุมชนแห่งประเทศไทยพร้อมตัวแทนประชาชนประมาณ 50 คน ได้เดินทางมมาที่ทำเนียบรัฐบาล เพื่อติดตามเร่งรัดความคืบหน้าที่ได้ร้องเรียนให้รัฐบาลช่วยเหลือทุนประกอบอาชีพให้ประชาชน|ตามโครงการสร้างคน สร้างงาน สร้างรายได้ ตามหลักปรัชญาเศรษฐกิจพอเพียง กลุ่มละ 1 ล้านบาท รวมทั้งให้ยุติการบังคับคดีเกี่ยวกับที่อยู่อาศัย|โดยให้ธนาคารของรัฐไถ่ถอนหรือซื้อคืนบ้าน ที่ทำกินให้กับประชาชน และผ่อนส่งราคาที่เป็นธรรมกับธนาคารของรัฐ และอนุญาตให้กู้เงินใช้หนี้นอกระบบให้กับประชาชนตามที่มีหนี้สินตามความเป็นจริง และแก้ปัญหาเรื่องบัตรเครดิต รถยนต์ รถมอเตอร์ไซค์ ที่ใช้ประกอบอาชีพจะโดนยึด เพื่อจะได้ใช้ประกอบอาชีพต่อไปได้|นายจำรัส กล่าวว่า ขอให้นายอภิสิทธิ์ เวชชาชีวะ นายกรัฐมนตรี มีบัญชาไปยังนายกอร์ปศักดิ์ สภาวสุ รองนายกรัฐมนตรี นายกรณ์ จาติกวณิช รมว.คลัง ดำเนินการช่วยเหลือประชาชนผู้เดือดร้อน|อีกทั้งนายกรณ์ เคยระบุว่า จะให้มีการตั้งธนาคารชุมชนเพื่อช่วยเหลือประชาชนที่ได้รับความเดือดร้อน ซึ่งตนเห็นด้วยที่จะมีการดำเนินการใ

In [ ]:
with open('gold-mt5-small-eng_prompt2.txt', 'w') as f:
  f.write(gold)
!cp 'gold-mt5-small-eng_prompt2.txt' '/content/drive/MyDrive/NLP 3 Project'

In [ ]:
[x for x in predicted.split('|') if x in gold.split('|')]

['ตำรวจกระจายกำลังตามจุดต่างๆ โดยรอบศาลฎีกา ก่อนพิจารณาคดีทุจริตกล้ายาง',
 'เจ้าหน้าที่ตำรวจกระจายกำลังตามจุดต่างๆ โดยรอบบริเวณศาลฎีกา ก่อนจะมีการพิจารณาคดีทุจริตการจัดซื้อโครงการกล้ายางพารา',
 'ทั้งนี้ ยังไม่มีกลุ่มคนเสื้อน้ำเงิน ที่จะเดินทางมาให้กำลังใจนายเนวิน ชิดชอบ จำเลยที่ 4 ของคดีดังกล่าวด้วย',
 'ประธานวุฒิสภา เชื่อ ศาลจะพิจารณาคดีทุจริตจัดซื้อต้นกล้ายางพาราตามกฎหมายและข้อเท็จจริง พร้อมระบุ ไม่ห่วงการยื่นถวายฎีกาขอพระราชทานอภัยโทษให้แก่อดีตนายกรัฐมนตรี',
 'ขณะที่ก่อนหน้านี้ที่ประชุมวุฒิสภา ยังได้มีมติเห็นชอบร่างพระราชบัญญัติคุ้มครองการดำเนินงานของสถาบันความร่วมมือเพื่อพัฒนาเศรษฐกิจลุ่มน้ำโขง โดยไม่มีการแก้เพิ่มเติม และยังเห็นชอบผ่านร่างพระราชบัญญัติแก้ไขเพิ่มเติมประมวลกฎหมายรัษฎากร ด้วย',
 'ตร.จร.แนะเลี่ยงเส้นทางหน้าพระลาน',
 'ตร.อนุญาตเสื้อแดง 50 คน เข้ายื่นรายชื่อ',
 'ขณะที่บริเวณศาลาว่าการ กทม. เสาชิงช้า ได้ให้เจ้าหน้าที่ดูแลความปลอดภัยโดยทั่วไป พร้อมเตรียมรถดับเพลิงไว้กว่า 10 คันด้วย',
 'นายชวรัตน์ ชาญวีรกูล รมว.มหาดไทย และหัวหน้าพรรคภูมิใจไทย กล่าวถึงการแต่งตั้งปลัดมหาดไทยค

In [ ]:
len([x for x in predicted.split('|') if x in gold.split('|')])

698

In [ ]:
len(predicted.split('|'))

2512

In [ ]:
len(gold.split('|'))

5251

In [ ]:
# Precision
# จำนวนที่ทำนายถูก / จำนวนที่ทำนายมาทั้งหมด
precision = len([x for x in predicted.split('|') if x in gold.split('|')]) / len(predicted.split('|'))
precision

0.2778662420382166

In [ ]:
# Recall
# จำนวนที่ทำนายถูก / จำนวนใน gold standard
recall = len([x for x in predicted.split('|') if x in gold.split('|')]) / len(gold.split('|'))
recall

0.13292706151209294

In [ ]:
# F1 = 2PR/(P+F)
f1_score = 2 * precision * recall / (precision + recall)
f1_score

0.17982738631972175